In [35]:
#PDFs That faced Error
#url='./PDF_FOLDER/Narasimha_Karumanchi_DS_Algo.pdf' -- error
#url="./PDF_FOLDER/Kubernetes_in_Action.pdf"
#url="./PDF_FOLDER/2022.acl-long.62.pdf"

In [36]:
#This url Variable is the input to the program
url="./PDF_SOURCE/Kubernetes_in_Action.pdf"

#Extraction if Document Name
doc_name=url.split('/')[-1]

In [37]:
import pymupdf # imports the pymupdf library
import pandas as pd 
import fitz  # import PyMuPDF

import numpy as np


import numpy as np
import matplotlib.pyplot as plt
import os
import json

In [38]:
###The Next Section is totally Decicated on Parsing of PDF to extract the text,images,tables.####
###After the PDF is parsed it is transformed to Dictionary Object for the storage of the parsed content.####

In [39]:
def show_image(item, title=""):
    """Display a pixmap.

    Just to display Pixmap image of "item" - ignore the man behind the curtain.

    Args:
        item: any PyMuPDF object having a "get_pixmap" method.
        title: a string to be used as image title

    Generates an RGB Pixmap from item using a constant DPI and using matplotlib
    to show it inline of the notebook.
    """
    DPI = 300  # use this resolution
    import numpy as np
    import matplotlib.pyplot as plt

    # %matplotlib inline
    pix = item.get_pixmap(dpi=DPI)
    img = np.ndarray([pix.h, pix.w, 3], dtype=np.uint8, buffer=pix.samples_mv)
    plt.figure(dpi=DPI)  # set the figure's DPI
    plt.title(title)  # set title of image
    _ = plt.imshow(img, extent=(0, pix.w * 72 / DPI, pix.h * 72 / DPI, 0))

In [40]:
def download_images_per_page(doc,doc_name,page,page_index,DPI):
    image_list = page.get_images()
    # print the number of images found on the page
    if image_list:
        print(f"Found {len(image_list)} images on page {page_index}")
    else:
        print("No images found on page", page_index)

    for image_index, img in enumerate(image_list, start=1): # enumerate the image list
        xref = img[0] # get the XREF of the image
        pix = pymupdf.Pixmap(doc, xref) # create a Pixmap
        #pix = pymupdf.Pixmap(doc.extract_image(xref)["image"])
        #mask = pymupdf.Pixmap(doc.extract_image(smask)["image"])
        #pix = pymupdf.Pixmap(pix1, mask)

        ### Commented Out Section for showing images################################
        #if pix.n - pix.alpha > 3: # CMYK: convert to RGB first
        #    pix = pymupdf.Pixmap(pymupdf.csRGB, pix)            
        # %matplotlib inline
        #pix = item.get_pixmap(dpi=DPI)
        #img = np.ndarray([pix.h, pix.w, 3], dtype=np.uint8, buffer=pix.samples_mv)
        #plt.figure(dpi=DPI)  # set the figure's DPI
        #plt.title(title)  # set title of image
        #_ = plt.imshow(img, extent=(0, pix.w * 72 / DPI, pix.h * 72 / DPI, 0))
        
        #############################################################################
            
        print('Image:')
        print(type(img))
            
        pix.save("./Parsed_PDF_Output/"+doc_name+"/"+"page_"+str(page_index+1)+"/image_%s.jpg" % (image_index)) # save the image as png
        pix = None
        
    return True
        

In [41]:
def extract_images_per_page(doc,doc_name,page_index,download):
    print("IN extract_images_per_page")
    page_image_dict={}
    page_number=page_index+1
    page = doc[page_index] # get the page by index
    
    ####Get Images along with the metadata of it in the following order:
    #(xref, smask, width, height, bpc, colorspace, alt. colorspace, name, filter, referencer)
    #xref (int) is the image object number
    #smask (int) is the object number of its soft-mask image
    #width and height (ints) are the image dimensions
    #bpc (int) denotes the number of bits per component (normally 8)
    #colorspace (str) a string naming the colorspace (like DeviceRGB)
    #alt. colorspace (str) is any alternate colorspace depending on the value of colorspace
    #name (str) is the symbolic name by which the image is referenced
    #filter (str) is the decode filter of the image (Adobe PDF References, pp. 22).
    #referencer (int) the xref of the referencer. Zero if directly referenced by the page. Only present if full=True.
    
    image_list = page.get_images(full=True) #full=True as it will give the if any other pages are referencing
                                            #the image.
    
    #for image in image_list:
    #    xref, smask, width, height, bpc, colorspace, alt_colorspace, name, filter, referencer=image
    #    print("width")
    #    print(width)
    ###########################################################################################################
    
    img_cnt=len(image_list)
    npy_img_lst=[]
    DPI=150
    title=""
    ###########Extraction Of Images in Numpy Format############
    
    for image_index, img in enumerate(image_list, start=1): # enumerate the image list
        
            img_meta_dict={}
            
            xref = img[0] # get the XREF of the image
            
            smask= img[1] # Get Object number of the Soft Mask of the Image
            
            width = img[2]
            print("width")
            print(width)
            
            height = img[3]
            print("height")
            print(height)
            
            num_bits = img[4] # Nuber of bits that is being used to represent the smallest component of the image
            colorspace = img[5] #colorspace of the image
            alt_colorspace = img[6] #colorspace of the image
            sym_name = img[7] #Symbolic name of the image
            img_filter = img[8] #decode filter of the image (Adobe PDF References, pp. 22)
            img_ref = img[9] #xref of the referencer. Zero if directly referenced by the page. 
                             #Only present if full=True.
                
            
            
            
            
            img_meta_dict["img_obj_num"]=xref
            img_meta_dict["smask_obj_num"]=smask
            img_meta_dict["width"]=width
            img_meta_dict["height"]=height
            img_meta_dict["num_bits"]=num_bits
            img_meta_dict["colorspace"]=colorspace
            img_meta_dict["alt_colorspace"]=alt_colorspace
            img_meta_dict["sym_name"]=sym_name
            img_meta_dict["filter"]=img_filter
            img_meta_dict["referencer"]=img_ref
            
            
            
            
            
            pix = pymupdf.Pixmap(doc, xref) # create a Pixmap
            
            #pix = pymupdf.Pixmap(doc.extract_image(xref)["image"])
            #mask = pymupdf.Pixmap(doc.extract_image(smask)["image"])
            #pix = pymupdf.Pixmap(pix1, mask)
            
            #pix.set_alpha(premultiply=False)
            
            ### Commented Out Section for showing images#############################

            if pix.n - pix.alpha > 3: # CMYK: convert to RGB first
                pix = pymupdf.Pixmap(pymupdf.csRGB, pix)
            # %matplotlib inline
            #pix = item.get_pixmap(dpi=DPI)
            
            print("PIX BUFFER SIZE")
            print(len(pix.samples_mv))
            
            
            image_size=(pix.h*pix.w*3)
            print('Original IMG_BUFFER_SIZE')
            print(image_size)
            
            print('Page Image Buffer Size')
            print(pix.samples_mv)
            
            #pix.size()=image_size
            
            try:
                img = np.ndarray([pix.h, pix.w, 3], dtype=np.uint8, buffer=pix.samples_mv)
            except:
                print('Image too large for Picture')
            finally:
                #img = np.ndarray([pix.h, pix.w, 3], dtype=np.uint8, buffer=pix.samples_mv)
                continue
            
            #plt.figure(dpi=DPI)  # set the figure's DPI
            #plt.title(title)  # set title of image
            #_ = plt.imshow(img, extent=(0, pix.w * 18 / DPI, pix.h * 18 / DPI, 0))
            
            #############################################################################
            
            #print('Image:')
            #print(type(img))
            
            #Encode the Image into Base64

            #img_enc = base64.b64encode(img)
            
            #For Decoding use the following statement 
            
            #decoded_image = base64.decodestring(img_enc)
            
            img_meta_dict["img_matrix"]=img
            
            npy_img_lst.append(img_meta_dict)
            
            #pix.save("page_%s-image_%s.png" % (page_index, image_index)) # save the image as png
            #pix = None
            
    
    ###########################################################
    
    page_image_dict['page']=page_number
    #page_image_dict['img_lst']=image_list
    page_image_dict['img_cnt']=len(image_list)
    page_image_dict['img_npy_lst']=npy_img_lst
    
    if download:
        download_images_per_page(doc,doc_name,page,page_index,DPI)
    
    return page_image_dict


def extract_text_tables_images_per_page(doc,doc_name,doc_img,index,download):
    print("IN extract_text_tables_images_per_page")
    page_dict={}
    page_image_dict={}
    tab_df_lst=[]
    page = doc[index]
    tabs = page.find_tables()  # detect the tables
    
    ##Extract Images From Pages############
    
    page_image_dict=extract_images_per_page(doc_img,doc_name,index,download)
    
    print("page_image_dict")
    print(page_image_dict)
    
    
    page_dict['page']=page_image_dict['page']
    #page_dict['img_lst']=page_image_dict['img_lst']

    page_dict['img_cnt']=page_image_dict['img_cnt']
    page_dict['img_npy_lst']=page_image_dict['img_npy_lst']
    
    #######################################
    
    ############################Extract Text#######################################################
    #Extract Text From each page
    text = page.get_text()
    page_dict['text']=text
    
    print(text)
    ###############################################################################################
    
    #for i,tab in enumerate(tabs):  # iterate over all tables
    #    for cell in tab.header.cells:
    #       page.draw_rect(cell,color=fitz.pdfcolor["red"],width=0.3)
    #    page.draw_rect(tab.bbox,color=fitz.pdfcolor["green"])
    #    print(f"Table {i} column names: {tab.header.names}, external: {tab.header.external}")
    
    #show_image(page, f"Table & Header BBoxes")
   
    # choose the second table for conversion to a DataFrame
    #tab = tabs[0]
    #print(tabs)
    
    if tabs.tables == []:
        print('Do Nothing')
    else:
        for tab in tabs:
            df=pd.DataFrame()
            df = tab.to_pandas()
            tab_df_lst.append(df)
    
    page_dict['tables']=tab_df_lst
    
    
    
    
    #print(tab_df_lst)
    #df = tab.to_pandas()
    # show the DataFrame
    return page_dict

In [42]:
#from numpyencoder import NumpyEncoder
import pickle
import shutil

def extract_text_images_tables(doc_path,download=False):
    
    doc_per_page_tabs_lst=[]
    doc = fitz.open(doc_path)
    
    num_pages=len(doc)
    
    doc_img = pymupdf.open(doc_path)
    
    doc_name=url.split('/')[-1]
    
    doc_type=url.split('.')[-1]
    
    doc_name_wo_type=url.split('/')[-1].split('.')[0]
    
    print(doc_name_wo_type)
    
    isExist = os.path.exists('./Parsed_PDF_Output/'+doc_name_wo_type)
    
    if isExist:
        shutil.rmtree('./Parsed_PDF_Output/'+doc_name_wo_type)
        
    os.mkdir('./Parsed_PDF_Output/'+doc_name_wo_type)
    
    for i in range(1,num_pages):
        #page_image_dict={}
        
        os.mkdir('./Parsed_PDF_Output/'+doc_name_wo_type+'/page_'+str(i+1))
        
        tab_df_lst=extract_text_tables_images_per_page(doc,doc_name_wo_type,doc_img,i,download)
        
        
        
        if len(tab_df_lst) == 0:
            print("Do Nothing Here")
        else: 
            doc_per_page_tabs_lst.append(tab_df_lst)
        
    
    
    document_dictionary={"name":doc_name,"type":doc_type, "data": doc_per_page_tabs_lst}

    if download:
        #Save the List of MetaData to pickle in disk.
        with open("./Parsed_PDF_Output/"+doc_name_wo_type+'/'+doc_name+'.pkl', 'wb') as f:
            pickle.dump(document_dictionary, f)
    
    return doc_per_page_tabs_lst

In [43]:
url

'./PDF_SOURCE/Kubernetes_in_Action.pdf'

In [44]:


document_dict=extract_text_images_tables(url,download=False)

Kubernetes_in_Action
IN extract_text_tables_images_per_page
IN extract_images_per_page
page_image_dict
{'page': 2, 'img_cnt': 0, 'img_npy_lst': []}
Kubernetes resources covered in the book
* Cluster-level resource (not namespaced)
** Also in other API versions; listed version is the one used in this book
(continues on inside back cover)
Resource (abbr.) [API version]
Description
Section
Namespace* (ns) [v1]
Enables organizing resources into non-overlapping 
groups (for example, per tenant)
3.7
Deploying workloads
Pod (po) [v1]
The basic deployable unit containing one or more 
processes in co-located containers
3.1
ReplicaSet (rs) [apps/v1beta2**]
Keeps one or more pod replicas running
4.3
ReplicationController (rc) [v1]
The older, less-powerful equivalent of a 
ReplicaSet
4.2
Job [batch/v1]
Runs pods that perform a completable task
4.5
CronJob [batch/v1beta1]
Runs a scheduled job once or periodically
4.6
DaemonSet (ds) [apps/v1beta2**]
Runs one pod replica per node (on all nodes or 
on

IN extract_images_per_page
page_image_dict
{'page': 22, 'img_cnt': 0, 'img_npy_lst': []}
CONTENTS
xx
18 
Extending Kubernetes
508
18.1
Defining custom API objects
508
Introducing CustomResourceDefinitions
509
■Automating 
custom resources with custom controllers
513
■Validating 
custom objects
517
■Providing a custom API server for your 
custom objects
518
18.2
Extending Kubernetes with the Kubernetes Service 
Catalog
519
Introducing the Service Catalog
520
■Introducing the 
Service Catalog API server and Controller Manager
521
Introducing Service Brokers and the OpenServiceBroker API
522
Provisioning and using a service
524
■Unbinding and 
deprovisioning
526
■Understanding what the Service 
Catalog brings
526
18.3
Platforms built on top of Kubernetes
527
Red Hat OpenShift Container Platform
527
■Deis Workflow 
and Helm
530
18.4
Summary
533
appendix A
Using kubectl with multiple clusters
534
appendix B
Setting up a multi-node cluster with kubeadm
539
appendix C
Using other container ru

IN extract_images_per_page
width
375
height
513
PIX BUFFER SIZE
577125
Original IMG_BUFFER_SIZE
577125
Page Image Buffer Size
page_image_dict
{'page': 31, 'img_cnt': 1, 'img_npy_lst': []}
xxix
about the author
Marko Lukša is a software engineer with more than 20 years of
professional experience developing everything from simple
web applications to full ERP systems, frameworks, and middle-
ware software. He took his first steps in programming back in
1985, at the age of six, on a second-hand ZX Spectrum com-
puter his father had bought for him. In primary school, he was
the national champion in the Logo programming competition
and attended summer coding camps, where he learned to pro-
gram in Pascal. Since then, he has developed software in a
wide range of programming languages.
   In high school, he started building dynamic websites when
the web was still relatively young. He then moved on to developing software for the
healthcare and telecommunications industries at a local company, w

IN extract_images_per_page
page_image_dict
{'page': 37, 'img_cnt': 0, 'img_npy_lst': []}
5
Understanding the need for a system like Kubernetes
DEPLOYING MICROSERVICES
As always, microservices also have drawbacks. When your system consists of only a
small number of deployable components, managing those components is easy. It’s
trivial to decide where to deploy each component, because there aren’t that many
choices. When the number of those components increases, deployment-related deci-
sions become increasingly difficult because not only does the number of deployment
combinations increase, but the number of inter-dependencies between the compo-
nents increases by an even greater factor. 
 Microservices perform their work together as a team, so they need to find and talk
to each other. When deploying them, someone or something needs to configure all of
them properly to enable them to work together as a single system. With increasing
numbers of microservices, this becomes tedious and erro

IN extract_images_per_page
page_image_dict
{'page': 44, 'img_cnt': 0, 'img_npy_lst': []}
12
CHAPTER 1
Introducing Kubernetes
and so on. This way, processes cannot hog resources reserved for other processes,
which is similar to when each process runs on a separate machine.
1.2.2
Introducing the Docker container platform
While container technologies have been around for a long time, they’ve become
more widely known with the rise of the Docker container platform. Docker was the
first container system that made containers easily portable across different machines.
It simplified the process of packaging up not only the application but also all its
libraries and other dependencies, even the whole OS file system, into a simple, por-
table package that can be used to provision the application to any other machine
running Docker. 
 When you run an application packaged with Docker, it sees the exact filesystem
contents that you’ve bundled with it. It sees the same files whether it’s running on
y

...

IN extract_text_tables_images_per_page
IN extract_images_per_page
page_image_dict
{'page': 609, 'img_cnt': 0, 'img_npy_lst': []}
INDEX
577
limiting resources (continued)
available to containers 412–416
exceeding limits 414–415
limits as seen by applications 
in containers 415–416
setting hard limits for 
resources containers can 
use 412–413
LimitRange objects, creating
422–423
limits
as seen by applications in 
containers 415–416
containers seeing all node 
CPU cores 416
containers seeing node 
memory 415–416
enforcing 423–424
exceeding 414–415
for pods per namespace, setting 
defaults 421–425
overcommitting 413
setting for resources used by 
containers 412–413
See also resource limits
Linux Control Groups 
(cgroups) 11
Linux Namespaces 11
Linux OS
container technologies, isolat-
ing components with 8
Namespaces, isolating pro-
cesses with 11
listing
all running containers 32
cluster nodes 40
clusters 538
container images 554–555
contexts 538
job instances in clusters 237–238
kube con

IN extract_images_per_page
page_image_dict
{'page': 613, 'img_cnt': 0, 'img_npy_lst': []}
INDEX
581
PersistentVolumes (continued)
dynamically provisioned 186–187
listing 180–181
pre-provisioned, Persistent-
VolumeClaims bound 
to 189
reclaiming automatically
183–184
reclaiming manually 183
recycling 183–184
Pet pods 295–299
communicating with pods 
through API servers
295–297
connecting to cluster-internal 
services through API 
servers 299
deleting 297–298
exposing through services
298–299
scaling StatefulSets 298
PetSets 284
photonPersistentDisk volume 163
PID namespaces 379–380
pinging service IP 131
platforms 527–533
Deis Workflow 530–533
Helm 530–533
Red Hat OpenShift Container 
platform 527–530
application templates
528–529
automatically deploying 
newly built images with 
DeploymentConfigs
529–530
building images from source 
using BuildConfigs 529
exposing services externally 
using Routes 530
groups 528
projects 528
resources available in 527–528
users 528
using 530
pod affini

IN extract_images_per_page
page_image_dict
{'page': 618, 'img_cnt': 0, 'img_npy_lst': []}
INDEX
586
replicating stateful pods 281–284
providing stable identity for 
pods 282–284
running multiple replicas with 
separate storage for 
each 281–282
replication controllers 47–48
replication managers 323–324
ReplicationControllers 90–104
benefits of using 93
changing pod templates 101
creating 93–94
creating new pods with 96
deleting 103–104
getting information about
95–96
horizontally scaling pods
102–103
in action 94–98
moving pods in and out of 
scope of 98–101
adding labels to pods man-
aged by 99
changing label selectors
100–101
changing labels of managed 
pod 99–100
removing pods from 
controllers 100
operation of 91–93
parts of 92–93
performing automatic 
rolling updates with
254–261
obsolescence of kubectl 
rolling-update
260–261
performing rolling updates 
with kubectl 256–260
running initial version of 
applications 254–255
reconciliation loops 92
replacing old pods with new 
pods 

IN extract_images_per_page
page_image_dict
{'page': 623, 'img_cnt': 0, 'img_npy_lst': []}
INDEX
591
services (continued)
listing 46
listing from pods 357
living outside cluster, connect-
ing to 131–134
overview 121–131
provisioning 524–526
requests hitting three pods 50
running applications through, 
using YAML file 255
signaling when pods ready to 
accept connections
149–153
testing from within cluster 124
troubleshooting 156
using 524–526
why needed 48
See also external services
sessionAffinity property 126
sessions, configuring affinity on 
services 126
set-context command 538
share-type label 467
sharing
data between containers with 
volumes 163–169
using emptyDir volume
163–166
using Git repository as start-
ing point for volume
166–169
volumes when containers 
running as different 
users 387–389
shell forms, versus exec forms
193–194
shells
running in containers 130–131
running inside existing 
containers 33
shutdown handlers, implement-
ing in applications 490–491
shutdown logic

IN extract_images_per_page
width
527
height
879
PIX BUFFER SIZE
1389699
Original IMG_BUFFER_SIZE
1389699
Page Image Buffer Size
width
527
height
1902
PIX BUFFER SIZE
3007062
Original IMG_BUFFER_SIZE
3007062
Page Image Buffer Size
width
786
height
601
PIX BUFFER SIZE
472386
Original IMG_BUFFER_SIZE
1417158
Page Image Buffer Size
Image too large for Picture
width
715
height
448
PIX BUFFER SIZE
320320
Original IMG_BUFFER_SIZE
960960
Page Image Buffer Size
Image too large for Picture
page_image_dict
{'page': 628, 'img_cnt': 4, 'img_npy_lst': []}
Marko Lukša
K
ubernetes is Greek for “helmsman,” your guide through 
unknown waters. The Kubernetes container orchestra-
tion system safely manages the structure and ﬂ
 ow of a 
distributed application, organizing containers and services for 
maximum efﬁ
 ciency. Kubernetes serves as an operating system 
for your clusters, eliminating the need to factor the underlying 
network and server infrastructure into your designs.
Kubernetes in Action teache

In [45]:
document_dict

[{'page': 2,
  'img_cnt': 0,
  'img_npy_lst': [],
  'text': 'Kubernetes resources covered in the book\n* Cluster-level resource (not namespaced)\n** Also in other API versions; listed version is the one used in this book\n(continues on inside back cover)\nResource (abbr.) [API version]\nDescription\nSection\nNamespace* (ns) [v1]\nEnables organizing resources into non-overlapping \ngroups (for example, per tenant)\n3.7\nDeploying workloads\nPod (po) [v1]\nThe basic deployable unit containing one or more \nprocesses in co-located containers\n3.1\nReplicaSet (rs) [apps/v1beta2**]\nKeeps one or more pod replicas running\n4.3\nReplicationController (rc) [v1]\nThe older, less-powerful equivalent of a \nReplicaSet\n4.2\nJob [batch/v1]\nRuns pods that perform a completable task\n4.5\nCronJob [batch/v1beta1]\nRuns a scheduled job once or periodically\n4.6\nDaemonSet (ds) [apps/v1beta2**]\nRuns one pod replica per node (on all nodes or \nonly on those matching a node selector)\n4.4\nStatefulSet 

In [48]:
#####Convert the dataframe content to list of dictionary#####
pdf_content_df=pd.DataFrame.from_dict(document_dict)

In [49]:
##############Pickle the list of dictionaries ############
import pickle


# Store data (serialize)
with open('pdf_content_dict_stage1.pickle', 'wb') as handle:
    pickle.dump(document_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

# Load data (deserialize)
with open('pdf_content_dict_stage1.pickle', 'rb') as handle:
    document_dict_deserialized = pickle.load(handle)

In [50]:
pdf_content_df=pd.DataFrame.from_dict(document_dict_deserialized)

[{'page': 2,
  'img_cnt': 0,
  'img_npy_lst': [],
  'text': 'Kubernetes resources covered in the book\n* Cluster-level resource (not namespaced)\n** Also in other API versions; listed version is the one used in this book\n(continues on inside back cover)\nResource (abbr.) [API version]\nDescription\nSection\nNamespace* (ns) [v1]\nEnables organizing resources into non-overlapping \ngroups (for example, per tenant)\n3.7\nDeploying workloads\nPod (po) [v1]\nThe basic deployable unit containing one or more \nprocesses in co-located containers\n3.1\nReplicaSet (rs) [apps/v1beta2**]\nKeeps one or more pod replicas running\n4.3\nReplicationController (rc) [v1]\nThe older, less-powerful equivalent of a \nReplicaSet\n4.2\nJob [batch/v1]\nRuns pods that perform a completable task\n4.5\nCronJob [batch/v1beta1]\nRuns a scheduled job once or periodically\n4.6\nDaemonSet (ds) [apps/v1beta2**]\nRuns one pod replica per node (on all nodes or \nonly on those matching a node selector)\n4.4\nStatefulSet 

In [ ]:
###The next Section focuses on How to map the text data parsed from PDF and make meaning out of it.###
###By Meaning we meaning context,important topics.keywords to which the daa belongs to.#####
###The main motto of the section is give meaningful representation to the data before it is fed to Graph Layer####

In [4]:
#####Importing the essential libraries for Topic Modelling ###########
from bertopic.representation import KeyBERTInspired, LlamaCPP  # Representation Comparison
from sentence_transformers import SentenceTransformer  # Embedding Model Wrapper
from cuml.manifold import UMAP  # For UMAP dimensionality reduction
from cuml.cluster import HDBSCAN  # For clustering with HDBSCAN
from bertopic import BERTopic  # For topic modeling with BERTopic

In [5]:
import PIL  # For image processing
import numpy as np  # For numerical computations
import requests  # For making HTTP requests
import datamapplot  # For data visualization
import re  # For regular expressions

In [20]:
###The next section Building theGraph from the parsed PDF and the Sematic Content and Contextual data####
import PIL  # For image processing
import numpy as np  # For numerical computations
import requests  # For making HTTP requests
import datamapplot  # For data visualization
import re  # For regular expressions

In [7]:
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader
from llama_index.llms.openai import OpenAI
from IPython.display import Markdown, display

In [32]:
from langchain_ollama import OllamaLLM

from langchain_ollama import OllamaLLM

from langchain_community.chat_models import ChatOllama
from langchain_core.messages import HumanMessage,SystemMessage,AIMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.prompts import ChatPromptTemplate

#llm = OllamaLLM(model="llama3.1")


llm = OllamaLLM(model="llama3.1")

from langchain_ollama import OllamaLLM

llm = OllamaLLM(model="llama3.1")

In [31]:
messages = [
    SystemMessage(content="You are very good Kubernetes expert.With your indepth knowledge of kuberetes \
    and cloud technology you will find out or extract relevant topics and keyphrases that explains input text chunk.\
    You will output the extratcted topics or keyphrases in form of an array and nothing else"),
    HumanMessage(
        content="15\nIntroducing container technologies\nthat each container has its own isolated filesystem. How can both app A and app B\nshare the same files?\nUNDERSTANDING IMAGE LAYERS\nI’ve already said that Docker images are composed of layers. Different images can con-\ntain the exact same layers because every Docker image is built on top of another\nimage and two different images can both use the same parent image as their base.\nThis speeds up the distribution of images across the network, because layers that have\nalready been transferred as part of the first image don’t need to be transferred again\nwhen transferring the other image. \n But layers don’t only make distribution more efficient, they also help reduce the\nstorage footprint of images. Each layer is only stored once. Two containers created\nfrom two images based on the same base layers can therefore read the same files, but\nif one of them writes over those files, the other one doesn’t see those changes. There-\nfore, even if they share files, they’re still isolated from each other. This works because\ncontainer image layers are read-only. When a container is run, a new writable layer is\ncreated on top of the layers in the image. When the process in the container writes to\na file located in one of the underlying layers, a copy of the whole file is created in the\ntop-most layer and the process writes to the copy. \nUNDERSTANDING THE PORTABILITY LIMITATIONS OF CONTAINER IMAGES\nIn theory, a container image can be run on any Linux machine running Docker, but\none small caveat exists—one related to the fact that all containers running on a host use\nthe host’s Linux kernel. If a containerized application requires a specific kernel version,\nit may not work on every machine. If a machine runs a different version of the Linux\nkernel or doesn’t have the same kernel modules available, the app can’t run on it.\n While containers are much more lightweight compared to VMs, they impose cer-\ntain constraints on the apps running inside them. VMs have no such constraints,\nbecause each VM runs its own kernel. \n And it’s not only about the kernel. It should also be clear that a containerized app\nbuilt for a specific hardware architecture can only run on other machines that have\nthe same architecture. You can’t containerize an application built for the x86 architec-\nture and expect it to run on an ARM-based machine because it also runs Docker. You\nstill need a VM for that.\n1.2.3\nIntroducing rkt—an alternative to Docker\nDocker was the first container platform that made containers mainstream. I hope I’ve\nmade it clear that Docker itself doesn’t provide process isolation. The actual isolation\nof containers is done at the Linux kernel level using kernel features such as Linux\nNamespaces and cgroups. Docker only makes it easy to use those features.\n After the success of Docker, the Open Container Initiative (OCI) was born to cre-\nate open industry standards around container formats and runtime. Docker is part\nof that initiative, as is rkt (pronounced “rock-it"
    )
]

In [33]:
sys_messages=[SystemMessage(content="You are very good Kubernetes expert.With your indepth knowledge of kuberetes \
    and cloud technology you will find out or extract relevant topics and keyphrases that explains input text chunk.\
    You will output the extratcted topics or keyphrases in form of an array")].append([HumanMessage(
        content="15\nIntroducing container technologies\nthat each container has its own isolated filesystem. How can both app A and app B\nshare the same files?\nUNDERSTANDING IMAGE LAYERS\nI’ve already said that Docker images are composed of layers. Different images can con-\ntain the exact same layers because every Docker image is built on top of another\nimage and two different images can both use the same parent image as their base.\nThis speeds up the distribution of images across the network, because layers that have\nalready been transferred as part of the first image don’t need to be transferred again\nwhen transferring the other image. \n But layers don’t only make distribution more efficient, they also help reduce the\nstorage footprint of images. Each layer is only stored once. Two containers created\nfrom two images based on the same base layers can therefore read the same files, but\nif one of them writes over those files, the other one doesn’t see those changes. There-\nfore, even if they share files, they’re still isolated from each other. This works because\ncontainer image layers are read-only. When a container is run, a new writable layer is\ncreated on top of the layers in the image. When the process in the container writes to\na file located in one of the underlying layers, a copy of the whole file is created in the\ntop-most layer and the process writes to the copy. \nUNDERSTANDING THE PORTABILITY LIMITATIONS OF CONTAINER IMAGES\nIn theory, a container image can be run on any Linux machine running Docker, but\none small caveat exists—one related to the fact that all containers running on a host use\nthe host’s Linux kernel. If a containerized application requires a specific kernel version,\nit may not work on every machine. If a machine runs a different version of the Linux\nkernel or doesn’t have the same kernel modules available, the app can’t run on it.\n While containers are much more lightweight compared to VMs, they impose cer-\ntain constraints on the apps running inside them. VMs have no such constraints,\nbecause each VM runs its own kernel. \n And it’s not only about the kernel. It should also be clear that a containerized app\nbuilt for a specific hardware architecture can only run on other machines that have\nthe same architecture. You can’t containerize an application built for the x86 architec-\nture and expect it to run on an ARM-based machine because it also runs Docker. You\nstill need a VM for that.\n1.2.3\nIntroducing rkt—an alternative to Docker\nDocker was the first container platform that made containers mainstream. I hope I’ve\nmade it clear that Docker itself doesn’t provide process isolation. The actual isolation\nof containers is done at the Linux kernel level using kernel features such as Linux\nNamespaces and cgroups. Docker only makes it easy to use those features.\n After the success of Docker, the Open Container Initiative (OCI) was born to cre-\nate open industry standards around container formats and runtime. Docker is part\nof that initiative, as is rkt (pronounced “rock-it"
    )])

In [34]:
response = llm.invoke(messages)
print(response)

```python
['Container Isolation', 'Shared Files in Containers', 'Image Layers', 'Distribution Efficiency', 'Storage Footprint Reduction', 'Portability Limitations of Container Images', 'Kernel Version Constraints', 'Hardware Architecture Constraints', 'Alternative to Docker', 'rkt', 'Open Container Initiative', 'OCI Standards', 'Process Isolation', 'Linux Namespaces', 'cgroups']
```


In [24]:
from pyvis.network import Network
import networkx as nx

G = nx.DiGraph()
G.add_node(1, label=doc_name , title='Document_Name' , color="red")


for keyval in page_dict:
    page_num="page_"+str(keyval['page'])
    
    G.add_node(page_num, label=str(keyval['page']), title=page_num,color="blue")
    G.add_edge(1,page_num)
    
    #Adding Text Node###
    node_name=page_num+"_text"
    G.add_node(node_name, label=node_name, title=str(keyval['text']), color="green")
    G.add_edge(page_num,node_name)
    
    #Adding Table Flag###
    node_name=page_num+"_table_flag"
    tab_list_len=len(keyval['tables'])
    
    if tab_list_len==0:
        G.add_node(node_name, label=node_name, title=str(keyval['img_cnt']),color="brown")
        G.add_edge(page_num,node_name)
    else:
        G.add_node(node_name, label=node_name, title=str(keyval['img_cnt']),color="green")
        G.add_edge(page_num,node_name)   
    
    #####Adding Image Flag####
    node_name=page_num+"_image_flag"
    image_cnt=keyval['img_cnt']
    
    if image_cnt==0:
        G.add_node(node_name, label=node_name, title=str(keyval['img_cnt']),color="black")
        G.add_edge(page_num,node_name)
    else:
        G.add_node(node_name, label=node_name, title=str(keyval['img_cnt']),color="green")
        G.add_edge(page_num,node_name)
    

In [25]:
nt = Network('800px', '2000px',notebook=True)
# populates the nodes and edges data structures
nt.from_nx(G)
nt.toggle_physics(True)
nt.show('nx1.html')

nx1.html


In [ ]:
from pyvis.network import Network
import networkx as nx

G = nx.DiGraph()

G.add_node(1, label=name , title='Document_Name' , color="red")

for i in range(2,len(result)):
    topic_name="Topic_"+str(i)
    content_name=topic_name+'_'+'content'
    G.add_node(topic_name, label=result[i].metadata['heading'] , title=result[i].metadata['heading'],color="blue")
    G.add_node(content_name, label=content_name , title=result[i].page_content, color="green")
    G.add_edge(1,topic_name)
    G.add_edge(topic_name,content_name)

In [ ]:
nt = Network('800px', '2000px',notebook=True)
# populates the nodes and edges data structures
nt.from_nx(G)
nt.toggle_physics(True)
nt.show('nx1.html')

In [ ]:
G